<a href="https://colab.research.google.com/github/Rumeysakeskin/Speech-Datasets-for-ASR/blob/main/download_mozilla_common_voice_for_turkish.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
# !sudo apt-get install libsox-fmt-all
!pip install install sox
!pip install wget
!sudo apt-get update && sudo apt-get install sox libsox-fmt-all

Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com
Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com


'sudo' is not recognized as an internal or external command,
operable program or batch file.


# Yeni Bölüm

In [ ]:
import sys
import argparse
import csv
import json
import logging
import multiprocessing
import os
import tarfile
from multiprocessing.pool import ThreadPool
from pathlib import Path
from typing import List

import sox
from sox import Transformer
import wget
from tqdm import tqdm

In [ ]:
parser = argparse.ArgumentParser(description='Downloads and processes Mozilla Common Voice dataset.')
parser.add_argument("--data_root", default='CommonVoice_dataset/', type=str, help="Directory to store the dataset.")
parser.add_argument('--manifest_dir', default='./', type=str, help='Output directory for manifests')
parser.add_argument("--num_workers", default=multiprocessing.cpu_count(), type=int, help="Workers to process dataset.")
parser.add_argument('--sample_rate', default=16000, type=int, help='Sample rate')
parser.add_argument('--files_to_process', nargs='+', default=['test.tsv', 'dev.tsv', 'train.tsv'],
                    type=str, help='list of *.csv file names to process')
parser.add_argument('--version', default='cv-corpus-11.0-2022-09-21',
                    type=str, help='Version of the dataset (obtainable via https://commonvoice.mozilla.org/en/datasets')
parser.add_argument('--language', default='tr',
                    type=str, help='Which language to download.(default english,'
                                   'check https://commonvoice.mozilla.org/en/datasets for more language codes')

# args = parser.parse_args()
args, unknown = parser.parse_known_args()

In [ ]:
# -------- CHANGE VERSION AND LANGUAGE
version = 'cv-corpus-11.0-2022-09-21'
language = 'cv-corpus-11.0-2022-09-21-tr'

COMMON_VOICE_URL = f"https://voice-prod-bundler-ee1969a6ce8178826482b88e843c335139bd3fb4.s3.amazonaws.com/" \
                   "{}/{}.tar.gz".format(version, language)

In [ ]:
def create_manifest(
        data: List[tuple],
        output_name: str,
        manifest_path: str):
    output_file = Path(manifest_path) / output_name
    output_file.parent.mkdir(exist_ok=True, parents=True)
    with output_file.open(mode='w', encoding="utf-8") as f:
        for wav_path, duration, text in tqdm(data, total=len(data)):
            f.write(
                json.dumps({
                    'audio_filepath': wav_path,
                    "duration": duration,
                    'text': text
                },  ensure_ascii=False) + '\n'
            )

def process_files(csv_file, data_root, num_workers):
    """ Read *.csv file description, convert mp3 to wav, process text.
        Save results to data_root.
    Args:
        csv_file: str, path to *.csv file with data description, usually start from 'cv-'
        data_root: str, path to dir to save results; wav/ dir will be created
    """
    wav_dir = os.path.join(data_root, 'wav/')
    os.makedirs(wav_dir, exist_ok=True)
    audio_clips_path = os.path.dirname(csv_file) + '/clips/'

    def process(x):
        file_path, text = x
        file_name = os.path.splitext(os.path.basename(file_path))[0]
        text = text.lower().strip()
        audio_path = os.path.join(audio_clips_path, file_path)
        output_wav_path = os.path.join(wav_dir, file_name + '.wav')

        tfm = Transformer()
        tfm.rate(samplerate=args.sample_rate)
        tfm.build(
            input_filepath=audio_path,
            output_filepath=output_wav_path
        )
        duration = sox.file_info.duration(output_wav_path)
        return output_wav_path, duration, text

    logging.info('Converting mp3 to wav for {}.'.format(csv_file))
    with open(csv_file, encoding="utf8") as csvfile:
        reader = csv.DictReader(csvfile, delimiter='\t')
        next(reader, None)  # skip the headers
        data = [(row['path'], row['sentence']) for row in reader]
        with ThreadPool(num_workers) as pool:
            data = list(tqdm(pool.imap(process, data), total=len(data)))

    print(data)
    return data

In [ ]:
def main():
    data_root = args.data_root
    os.makedirs(data_root, exist_ok=True)

    target_unpacked_dir = os.path.join(data_root, "CV_unpacked")

    if os.path.exists(target_unpacked_dir):
        print('Find existing folder {}'.format(target_unpacked_dir))
    else:
        print("Could not find Common Voice, Downloading corpus...")

        filename = wget.download(COMMON_VOICE_URL, data_root)
        target_file = os.path.join(data_root, os.path.basename(filename))

        os.makedirs(target_unpacked_dir, exist_ok=True)
        print("Unpacking corpus to {} ...".format(target_unpacked_dir))
        tar = tarfile.open(target_file, encoding="utf8")
        tar.extractall(target_unpacked_dir)
        tar.close()

    folder_path = os.path.join(target_unpacked_dir, args.version + f'/{args.language}/')

    for csv_file in args.files_to_process:
        data = process_files(
            csv_file=os.path.join(folder_path, csv_file),
            data_root=os.path.join(data_root, os.path.splitext(csv_file)[0]),
            num_workers=args.num_workers
        )
        logging.info('Creating manifests...')
        create_manifest(
            data=data,
            output_name=f'commonvoice_{os.path.splitext(csv_file)[0]}_manifest.jsonl',
            manifest_path=args.manifest_dir,
        )


if __name__ == "__main__":
    main()

Could not find Common Voice, Downloading corpus...
Unpacking corpus to CommonVoice_dataset/CV_unpacked ...


100%|██████████| 10142/10142 [05:21<00:00, 31.52it/s]


[('CommonVoice_dataset/test/wav/common_voice_tr_23660893.wav', 8.112, 'hayatta küçük şeyleri kovalıyor ve yine küçük şeyler için birbirimizi incitiyoruz.'), ('CommonVoice_dataset/test/wav/common_voice_tr_17343923.wav', 3.072, 'seydiu şimdi iki mevkiyi de kaybetti.'), ('CommonVoice_dataset/test/wav/common_voice_tr_26078972.wav', 2.88, 'ancak üç sezon sonra ligden ayrıldılar.'), ('CommonVoice_dataset/test/wav/common_voice_tr_23388477.wav', 6.84, 'katilin basitçe “canavar” olarak bilinen büyük bir hayvan olduğu düşünülüyordu.'), ('CommonVoice_dataset/test/wav/common_voice_tr_23650401.wav', 6.84, 'fakat öte yandan, hayatta gelişim sağlayabilmek için kendimi ne kadar çok strese soktuğumu farkediyorum.'), ('CommonVoice_dataset/test/wav/common_voice_tr_25887910.wav', 4.824, 'bahse girerim uzaklara gönderilen bir hediye.'), ('CommonVoice_dataset/test/wav/common_voice_tr_19942053.wav', 4.464, 'siyasette temiz insanlara ihtiyacımız var.'), ('CommonVoice_dataset/test/wav/common_voice_tr_29039679.

100%|██████████| 9577/9577 [05:16<00:00, 30.25it/s]


[('CommonVoice_dataset/dev/wav/common_voice_tr_28978303.wav', 8.784, 'hacer de çömelmiş, avucuyla su alarak yüzüne ve şakaklarındaki saçlara sürüyordu.'), ('CommonVoice_dataset/dev/wav/common_voice_tr_28978304.wav', 4.644, 'çalışanın yatanda hakkı vardır.'), ('CommonVoice_dataset/dev/wav/common_voice_tr_28978305.wav', 3.42, 'sonra birçok da sıra bekleyen var.'), ('CommonVoice_dataset/dev/wav/common_voice_tr_28978728.wav', 4.032, 'bir belagat numunesi.'), ('CommonVoice_dataset/dev/wav/common_voice_tr_28978729.wav', 8.1, 'bir zamanlar boş gezmeyi iş yapmaktan çok seven üç arkadaş varmış.'), ('CommonVoice_dataset/dev/wav/common_voice_tr_28978731.wav', 5.22, 'genç kadına doğru yürüyerek onun koluna yapıştı:'), ('CommonVoice_dataset/dev/wav/common_voice_tr_28978733.wav', 4.284, 'allahım, bu çok güzel.'), ('CommonVoice_dataset/dev/wav/common_voice_tr_28978734.wav', 3.492, 'kapı hafifçe aralandı.'), ('CommonVoice_dataset/dev/wav/common_voice_tr_28978755.wav', 3.312, 'kızınız…'), ('CommonVoice

100%|██████████| 25866/25866 [15:03<00:00, 28.62it/s]


[('CommonVoice_dataset/train/wav/common_voice_tr_28856095.wav', 3.6, 'çok kolaydır.'), ('CommonVoice_dataset/train/wav/common_voice_tr_28856097.wav', 3.564, 'kendimi kötü hissediyorum.'), ('CommonVoice_dataset/train/wav/common_voice_tr_28856098.wav', 3.132, 'artık seni tanıyamıyorum.'), ('CommonVoice_dataset/train/wav/common_voice_tr_28856099.wav', 4.644, 'maksat sırf memlekete hayırlı bir evlat yetiştirmek…'), ('CommonVoice_dataset/train/wav/common_voice_tr_28856106.wav', 2.592, 'nedeni bu.'), ('CommonVoice_dataset/train/wav/common_voice_tr_28856107.wav', 5.724, 'sadece vızıldayarak ağlıyor, anlaşılmaz küfürler mırıldanıyordu.'), ('CommonVoice_dataset/train/wav/common_voice_tr_28856108.wav', 2.664, 'bu nasıl olacak?'), ('CommonVoice_dataset/train/wav/common_voice_tr_28856109.wav', 2.7, 'burası özel mülk.'), ('CommonVoice_dataset/train/wav/common_voice_tr_28856110.wav', 2.124, 'i̇yi eğlenin.'), ('CommonVoice_dataset/train/wav/common_voice_tr_28856127.wav', 2.124, 'i̇t onu!'), ('CommonV

100%|██████████| 25866/25866 [00:00<00:00, 74754.20it/s]


In [ ]:
!zip -r /content/CommonVoice_dataset/train.zip /content/CommonVoice_dataset/train
!zip -r /content/CommonVoice_dataset/dev.zip /content/CommonVoice_dataset/dev
!zip -r /content/CommonVoice_dataset/test.zip /content/CommonVoice_dataset/test


Görüntülenen çıkış son 5000 satıra kısaltıldı.
  adding: content/CommonVoice_dataset/test/wav/common_voice_tr_28064017.wav (deflated 21%)
  adding: content/CommonVoice_dataset/test/wav/common_voice_tr_17559437.wav (deflated 34%)
  adding: content/CommonVoice_dataset/test/wav/common_voice_tr_21325203.wav (deflated 17%)
  adding: content/CommonVoice_dataset/test/wav/common_voice_tr_33526921.wav (deflated 28%)
  adding: content/CommonVoice_dataset/test/wav/common_voice_tr_20516226.wav (deflated 31%)
  adding: content/CommonVoice_dataset/test/wav/common_voice_tr_28859135.wav (deflated 29%)
  adding: content/CommonVoice_dataset/test/wav/common_voice_tr_20763770.wav (deflated 55%)
  adding: content/CommonVoice_dataset/test/wav/common_voice_tr_20022821.wav (deflated 14%)
  adding: content/CommonVoice_dataset/test/wav/common_voice_tr_28090827.wav (deflated 32%)
  adding: content/CommonVoice_dataset/test/wav/common_voice_tr_17393316.wav (deflated 18%)
  adding: content/CommonVoice_dataset/test/

In [ ]:
from google.colab import files
# files.download('/content/CommonVoice_dataset/dev.zip')
files.download('/content/CommonVoice_dataset/test.zip')
# files.download('/content/CommonVoice_dataset/train.zip')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
from google.colab import files
# files.download('/content/CommonVoice_dataset/dev.zip')
files.download('/content/CommonVoice_dataset/test.zip')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>